In [1]:
import pandas as pd
from pandas.api.types import CategoricalDtype
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
import contextily as cx
import mapclassify

plt.style.use('default')
# This next line tells jupyter to render the images inline
%matplotlib inline
import matplotlib_inline
# This renders your figures as vector graphics AND gives you an option to download a PDF too
matplotlib_inline.backend_inline.set_matplotlib_formats('svg', 'pdf')

In [2]:
trax1_df = pd.read_csv('data/aq_data/TRX01_2022_01.csv')
trax2_df = pd.read_csv('data/aq_data/TRX02_2022_01.csv')
trax3_df = pd.read_csv('data/aq_data/TRX03_2022_01.csv')
bus1_df = pd.read_csv('data/aq_data/BUS01_2022_01.csv')

In [3]:
#trax1_df

In [4]:
investigate_date = "2022-01-13"

trax1_df = trax1_df[trax1_df['Date'] == investigate_date].reset_index()
trax2_df = trax2_df[trax2_df['Date'] == investigate_date].reset_index()
trax3_df = trax3_df[trax3_df['Date'] == investigate_date].reset_index()
bus1_df = bus1_df[bus1_df['Date'] == investigate_date].reset_index()

#put all these data frames into one
concat_df = pd.concat([trax1_df, trax2_df, trax3_df, bus1_df], ignore_index=True)
concat_df['Timestamp_UTC'] = pd.to_datetime(concat_df['Timestamp_UTC'])
concat_df['Hour'] = concat_df['Timestamp_UTC'].apply(lambda x: x.timetuple().tm_hour)
concat_df['Timestamp_UTC'] = concat_df['Timestamp_UTC'].astype(str)

In [5]:
concat_df['AQI'] = concat_df['ES642_PM2.5_Concentration_ug/m3'].apply(lambda x: 
                                                                  'Good' if x < 12 
                                                                        else ('Moderate' if x < 35.5 
                                                                              else ('Unhealthy for Sensitive Groups' if x < 55.5 
                                                                                    else ('Unhealthy' if x < 150.5
                                                                                          else ('Very Unhealthy' if x < 250.5 
                                                                                                else 'Hazardous')))))

concat_df['PM2.5_Category'] = concat_df['ES642_PM2.5_Concentration_ug/m3'].apply(lambda x:
                                                                                 '< 12.00' if x < 12.00
                                                                                    else ('12.00 - 35.50' if x < 35.50
                                                                                          else('35.50 - 85.50' if x < 85.50
                                                                                                else('115.00 - 150.50') if x < 150.50
                                                                                                      else('150.50+'))))

In [6]:
check = concat_df.sort_values(by=['ES642_PM2.5_Concentration_ug/m3'], ascending=False).reset_index()
check = check['ES642_PM2.5_Concentration_ug/m3']
check

0       191.0
1        96.0
2        72.0
3        71.0
4        71.0
        ...  
4160      2.0
4161      2.0
4162      2.0
4163      2.0
4164      1.0
Name: ES642_PM2.5_Concentration_ug/m3, Length: 4165, dtype: float64

In [7]:
AQI_category = CategoricalDtype(categories=["Good", "Moderate", "Unhealthy for Sensitive Groups", "Unhealthy", "Very Unhealthy", "Hazardous"], ordered=True)
PM25_Category = CategoricalDtype(categories=["< 12.00", "12.00 - 35.50", "35.50 - 85.50", "115.00 - 150.50", "150.50+"], ordered=True)

In [8]:
concat_df['AQI'] = concat_df['AQI'].astype(AQI_category)
concat_df['PM2.5_Category'] = concat_df['PM2.5_Category'].astype(PM25_Category)

In [9]:
geo_df = gpd.GeoDataFrame(
    concat_df,
    geometry=gpd.points_from_xy(concat_df.Longitude_ddeg, concat_df.Latitude_ddeg),
    crs='EPSG:4326'
)

In [10]:
concat_df = concat_df[concat_df['Hour'] == 12]
concat_df

index        Timestamp_UTC  Latitude_ddeg  Longitude_ddeg  Elevation_m  \
686   16596  2022-01-13 12:01:44      40.543827     -112.013916       1458.8   
687   16597  2022-01-13 12:03:44      40.543926     -112.014023       1458.1   
688   16598  2022-01-13 12:05:44      40.543926     -112.014023       1457.9   
689   16599  2022-01-13 12:07:44      40.543926     -112.014023       1458.0   
690   16600  2022-01-13 12:09:44      40.543926     -112.014015       1458.1   
...     ...                  ...            ...             ...          ...   
3913   4250  2022-01-13 12:47:40      40.751961     -111.914490       1286.5   
3914   4251  2022-01-13 12:50:10      40.742474     -111.916885       1285.2   
3915   4252  2022-01-13 12:52:40      40.731396     -111.916931       1286.5   
3916   4253  2022-01-13 12:57:15      40.732777     -111.939064       1289.0   
3917   4254  2022-01-13 12:59:45      40.733166     -111.945213       1289.0   

      Battery_Voltage_volts  Train_Box_Temperature_degC  \
686                   14.05                        3.06   
687                   14.05                        3.06   
688                   14.03                        3.06   
689                   14.04                        3.06   
690                   14.05                        3.06   
...                     ...                         ...   
3913                  13.29                         NaN   
3914                  13.31                         NaN   
3915                  13.32                         NaN   
3916                  13.34                         NaN   
3917                  13.34                         NaN   

      Train_Top_Relative_Humidity_%  Train_Top_Temperature_degC  \
686                           65.91                       -0.64   
687                           66.99                       -0.77   
688                           68.45                       -1.05   
689                           68.48                       -1.08   
690                           69.40                       -1.32   
...                             ...                         ...   
3913                            NaN                         NaN   
3914                            NaN                         NaN   
3915                            NaN                         NaN   
3916                            NaN                         NaN   
3917                            NaN                         NaN   

      ES642_PM2.5_Concentration_ug/m3  ...  2B405_NO2_Concentration_ppbv  \
686                              11.0  ...                           NaN   
687                              11.0  ...                           NaN   
688                              12.0  ...                           NaN   
689                              12.0  ...                           NaN   
690                              10.0  ...                           NaN   
...                               ...  ...                           ...   
3913                             38.0  ...                          78.8   
3914                             34.0  ...                          22.0   
3915                             34.0  ...                          36.1   
3916                             38.0  ...                         -18.1   
3917                             39.0  ...                          17.3   

      2B405_NOX_Concentration_ppbv  2B405_Internal_Air_Temperature_degC  \
686                            NaN                                  NaN   
687                            NaN                                  NaN   
688                            NaN                                  NaN   
689                            NaN                                  NaN   
690                            NaN                                  NaN   
...                            ...                                  ...   
3913                         194.7                                 15.9   
3914              

In [11]:
""" fig, ax = plt.subplots(figsize=(7,7))
slv = cx.Place(search="Salt Lake", source=cx.providers.CartoDB.Positron, zoom=12)
slv.plot(ax = ax)

geo_df.to_crs(epsg=3857).plot(
    ax=ax,
    column='ES642_PM2.5_Concentration_ug/m3',
    #column='Elevation_m',
    cmap = 'plasma',
    legend=True
) 
 """

' fig, ax = plt.subplots(figsize=(7,7))\nslv = cx.Place(search="Salt Lake", source=cx.providers.CartoDB.Positron, zoom=12)\nslv.plot(ax = ax)\n\ngeo_df.to_crs(epsg=3857).plot(\n    ax=ax,\n    column=\'ES642_PM2.5_Concentration_ug/m3\',\n    #column=\'Elevation_m\',\n    cmap = \'plasma\',\n    legend=True\n) \n '

In [12]:
""" def my_colormap(value):  
    if value < 12:
        return "green"
    elif value < 55.5:
        return "yellow"
    elif value < 150.5:
        return "orange"
    elif value < 250.5:
        return "purple"
    else:
        return "maroon" """

' def my_colormap(value):  \n    if value < 12:\n        return "green"\n    elif value < 55.5:\n        return "yellow"\n    elif value < 150.5:\n        return "orange"\n    elif value < 250.5:\n        return "purple"\n    else:\n        return "maroon" '

In [13]:
geo_df.explore(
    column='AQI',
    #column='PM2.5_Category',
    #column='ES642_PM2.5_Concentration_ug/m3',
    #cmap= my_colormap,
    cmap=['green', 'yellow', 'orange', 'red', 'purple', 'maroon'],
    marker_type='circle_marker',
    marker_kwds={'radius': 5, 'fill': True, 'alpha': 1},
    #scheme='user_defined',
    #k = 5,
    style_kwds={'fillOpacity': 1, 'weight': 1, 'color': 'black'},
)